# CSIDH

In [265]:
set_verbose(-1)

In [266]:
load('file2load.sage')
import time

In [157]:
#----------------------------------------------------------------
#----------------------------------------------------------------
#----------------------------------------------------------------
#----------------------------------------------------------------


#CSIDH algorithm
#two parts part1 and part2
#they agree on prime p in form 4*(product of small odd primes numbers)-1
#both generate their private key --> n-tuples of numbers in range -m to m (m=5)
#starting curve E0: y2=x3+x over field Fp
#compute their isogeny walk in graph according to their private keys and get coefficients A (part1) and B (part2) --> public keys
#exchange this information --> part1 get B and part2 get A
#compute their isogeny walk in graph according to their private keys, part1 starts at EB: y2 = x3+Bx2+x, part2 starts at EA: y2 = x3+Ax2+x
#get coefficients BA (part1) and AB (part2)--> in fact AB=BA=S --> shared secret

Let's start with generating of a prime number p. 

In [267]:
[primes_list, p,a] = makePrimesList(30) # a == the smallest prime number bigger than the n-th prime number such that
# p is prime number, n is the only one parameter of makePrimesList(n)
print('List of primes:', primes_list)
print('Prime p:', p)
F = GF(p) #field

List of primes: [3, 5, 7, 11, 13, 17, 19, 23, 29, 31, 37, 41, 43, 47, 53, 59, 61, 67, 71, 73, 79, 83, 89, 97, 101, 103, 107, 109, 113, 127, 163]
Prime p: 1308719482222569797644787830882490714546558590759979


The starting curve is the one with the coefficient T = 0.

In [268]:
T=0 #starting curve E: y2 = x3 +Tx2+x

Generating keys.

In [269]:
# keyA =  [4, 0, -3, -2, -3, -3, 0, -3, 4, -4, -5, -3, 4, 3, -4, 5, -5, 1, 4, -1, 1, 1, 0, -2, 4, 3, -5, 4, 5, 4, 5, 0, 5, -4, 3, -1, 3, -2, 2, -4, 2, 1, -2, 1, -1, 5, 4, 0, -1, 3, 3, 3, 4, 4, -4, -3, -4, -3, -4, -4, -1, 4, -5, -4, -1, 2, -2, 2, -4, 0, 2, 2, 1, 2]
keyA = privateKeyGenerator(primes_list,5) #private key
keyBA = copy(keyA)
keyA1 = copy(keyA)
keyBA1 = copy(keyA)
# keyB = [-4, 5, 0, -4, -5, 2, 4, -5, 1, -5, -2, -3, -1, -3, 1, -4, 2, -2, -4, 4, 5, 3, -1, -2, -2, -4, -1, 5, 1, 0, 4, 5, 2, 4, -5, 2, 5, -2, -1, -5, 4, 3, -4, 5, -3, -1, -1, 1, -4, -5, 5, 3, 2, -1, 3, -4, -3, 2, 1, -3, -2, 2, 5, 2, 5, 2, -2, -1, 1, 4, -4, -4, 4, 5]
keyB = privateKeyGenerator(primes_list,5) #private key
keyAB = copy(keyB)
keyB1 = copy(keyB)
keyAB1 = copy(keyB)
print('Key A:', keyA)
print('Key B:', keyB)

Key A: [3, 5, 0, 0, 3, 1, -4, 0, -5, 1, 0, -3, 5, -2, 0, 2, -4, 4, 0, -5, 2, -5, -3, -5, 0, -5, 1, 2, -4, 0, -2]
Key B: [1, -3, 2, -1, 0, -1, 4, -2, 5, -4, 2, -3, 3, -5, 5, -2, -1, 0, 0, -2, -5, 4, 5, 5, 3, -3, -4, -5, 4, 4, 0]


According to the key, each part makes the walk in the isogeny graph.

In [270]:
z1 = time.time()
EA = MontgomeryCurve(F,T).classGroupEvaluation(keyA,primes_list)
EB = MontgomeryCurve(F,T).classGroupEvaluation(keyB,primes_list)
z2 = time.time()
A = EA.coef()
B = EB.coef()

In [271]:
EA

Montgomery elliptic curve defined by y^2 = x^3 + 786960503559987036011293402015453281414676581481854*x^2 + x  over finite field of size 1308719482222569797644787830882490714546558590759979.

In [272]:
EB

Montgomery elliptic curve defined by y^2 = x^3 + 662812809605980282600482912528193637126458939193888*x^2 + x  over finite field of size 1308719482222569797644787830882490714546558590759979.

In [273]:
timeT = z2 - z1
timeT

0.931628942489624

Both parts send their coefficient (public key) to the other part. We can simply validate, if each part have got valid key. And then isogeny walk again.

In [274]:
z3 = time.time()
if(EA.is_supersingular(primes_list) & EB.is_supersingular(primes_list)):
    # print 'PublicKey validation: successfull!'
    EAB = MontgomeryCurve(F,A).classGroupEvaluation(keyAB,primes_list)
    EBA = MontgomeryCurve(F,B).classGroupEvaluation(keyBA,primes_list)
    print('The isogeny walk of Part1 ends in the curve: ', EBA)
    print('The isogeny walk of Part2 ends in the curve: ', EAB)
    
    AB = EAB.coef()
    BA = EBA.coef()
    S=sharedSecret(AB,BA)
    print('Shared secret is: ', S)
# else:
    # print 'PublicKey validation: failed!'
z4 = time.time()

The isogeny walk of Part1 ends in the curve:  Montgomery elliptic curve defined by y^2 = x^3 + 1264253803369838612822442027104190206381170531236775*x^2 + x  over finite field of size 1308719482222569797644787830882490714546558590759979.
The isogeny walk of Part2 ends in the curve:  Montgomery elliptic curve defined by y^2 = x^3 + 1264253803369838612822442027104190206381170531236775*x^2 + x  over finite field of size 1308719482222569797644787830882490714546558590759979.
Shared secret is:  1264253803369838612822442027104190206381170531236775


In [166]:
timeT2 = z4 - z3
timeT2

1.0696635246276855

In [167]:
AB

723690234041187576818006398814186067992525160105562

In [168]:
BA

723690234041187576818006398814186067992525160105562

In [169]:
S

723690234041187576818006398814186067992525160105562

In [170]:
timeT + timeT2

1.8889639377593994

### CSIDH with Velu's

In [171]:
T = 0

In [172]:
z1 = time.time()
[EA,A] = classGroupEvaluation(T,keyA1,primes_list,F,p, 'Velu')
[EB,B] = classGroupEvaluation(T,keyB1,primes_list,F,p, 'Velu')
z2 = time.time()

[5, 4, -1, 2, 1, 5, -4, -3, -1, 1, -1, 3, -2, -3, 0, 3, 4, -4, 5, 4, 4, 3, -4, -3, 4, -5, 0, 1, -4, 0, 0]
Isogeny of degree 3 from Elliptic Curve defined by y^2 = x^3 + x over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 1193655162601740558747714196328548266004204665530685*x + 643769813363517536022470445064313432603253904369209 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 5 from Elliptic Curve defined by y^2 = x^3 + 1193655162601740558747714196328548266004204665530685*x + 643769813363517536022470445064313432603253904369209 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 1154313493932868263591394325671867549859398977769212*x + 877129170000547586310909939792840517636278282149917 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 11 from Elliptic Curve 

Isogeny of degree 29 from Elliptic Curve defined by y^2 = x^3 + 1285066987115630934032398073039458059305660359182392*x^2 + 415628420102527755051196217901270230270195454334097*x + 704406245549160797816581939574818687881060297033372 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 1285066987115630934032398073039458059305660359182392*x^2 + 1142710716918411465474739666241895271165838455602823*x + 368014752547959617227870371035650724313701391584347 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 37 from Elliptic Curve defined by y^2 = x^3 + 1285066987115630934032398073039458059305660359182392*x^2 + 1142710716918411465474739666241895271165838455602823*x + 368014752547959617227870371035650724313701391584347 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 12850669871156309340323980730394580593056603591823

Isogeny of degree 61 from Elliptic Curve defined by y^2 = x^3 + 62817987588679628622715287164829783846411219321579*x^2 + 1031400169954088476651038952746045704202356906910532*x + 1104092327598502161429092585051529825582942400138512 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 62817987588679628622715287164829783846411219321579*x^2 + 862583781192386995105533667979706265045447451783838*x + 823777425361187910403551351115140033555264446765443 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 71 from Elliptic Curve defined by y^2 = x^3 + 62817987588679628622715287164829783846411219321579*x^2 + 862583781192386995105533667979706265045447451783838*x + 823777425361187910403551351115140033555264446765443 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 62817987588679628622715287164829783846411219321579*x^2 +

[4, 2, 0, 0, 0, 3, -2, -2, 0, 0, 0, 1, 0, -1, 0, 1, 2, -2, 3, 2, 2, 1, -2, -1, 2, -3, 0, 0, -2, 0, 0]
Isogeny of degree 5 from Elliptic Curve defined by y^2 = x^3 + 226212876259634786363829370809347724650684261282684*x^2 + x over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 226212876259634786363829370809347724650684261282684*x^2 + 264209637220620665460113395763032022576095961811710*x + 956889190571860357602990375383985717588516948893202 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 17 from Elliptic Curve defined by y^2 = x^3 + 226212876259634786363829370809347724650684261282684*x^2 + 264209637220620665460113395763032022576095961811710*x + 956889190571860357602990375383985717588516948893202 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 226212876259634786363829370809347724650684261282684*x^2 + 40

Isogeny of degree 5 from Elliptic Curve defined by y^2 = x^3 + 168157502278730801234199431088835372854672317854086*x^2 + 334770346904191548771668005324978898777870907459727*x + 1029907012910611130104684715118266358528096931299140 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 168157502278730801234199431088835372854672317854086*x^2 + 1215709823262845371546133416974626879297945499338584*x + 381992540412485362086771954403748618453270059139018 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 17 from Elliptic Curve defined by y^2 = x^3 + 168157502278730801234199431088835372854672317854086*x^2 + 1215709823262845371546133416974626879297945499338584*x + 381992540412485362086771954403748618453270059139018 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 168157502278730801234199431088835372854672317854086*x

[1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Isogeny of degree 3 from Elliptic Curve defined by y^2 = x^3 + 1082439736079023209444336873671648324783498646366284*x^2 + x over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 1082439736079023209444336873671648324783498646366284*x^2 + 1304318105305685018043429952167699091058635322870855*x + 518196428316978138438492032339662644245305624099061 over Finite Field of size 1308719482222569797644787830882490714546558590759979
[-4, -3, 3, 0, -4, 5, -4, -5, 0, 1, 0, -2, 3, -4, -1, 2, 2, -1, 0, -5, 2, 5, 5, 2, 0, 0, -2, 4, -1, 0, -5]
Isogeny of degree 7 from Elliptic Curve defined by y^2 = x^3 + x over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 431708538736492255739019806699718996908238986589994*x + 248887540359918584408333550316649061264328729390964 over Finite Fie

Isogeny of degree 53 from Elliptic Curve defined by y^2 = x^3 + 786776627741084332225828697505900826513237170913474*x^2 + 248042424593445699220768762188748284460833176239073*x + 998868941332670014448467043456312216573103755763540 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 786776627741084332225828697505900826513237170913474*x^2 + 406762841939339525108150187539463441493395642742148*x + 261604480547201490364170292230664068960151924910438 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 67 from Elliptic Curve defined by y^2 = x^3 + 786776627741084332225828697505900826513237170913474*x^2 + 406762841939339525108150187539463441493395642742148*x + 261604480547201490364170292230664068960151924910438 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 786776627741084332225828697505900826513237170913474*x^2

Isogeny of degree 13 from Elliptic Curve defined by y^2 = x^3 + 1172399821933837900710068761496899411385959083076466*x^2 + 219858584132653732457477169395846245335064133568583*x + 1236600059942113828234152102350686515942219365338559 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 1172399821933837900710068761496899411385959083076466*x^2 + 1062324398812883256259095676226464256467374997128884*x + 776690471242150486249774438842775855826063646634882 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 19 from Elliptic Curve defined by y^2 = x^3 + 1172399821933837900710068761496899411385959083076466*x^2 + 1062324398812883256259095676226464256467374997128884*x + 776690471242150486249774438842775855826063646634882 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 1172399821933837900710068761496899411385959083076

Isogeny of degree 73 from Elliptic Curve defined by y^2 = x^3 + 529063144424448293493660300794910736859475405192249*x^2 + 474385189121216268344439056101097930861807258575900*x + 1292448962967544402258225904706868325809556312632198 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 529063144424448293493660300794910736859475405192249*x^2 + 368219417368925678040417516301925917412126306519292*x + 691475525517129862790186451321330630700919158856758 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 163 from Elliptic Curve defined by y^2 = x^3 + 529063144424448293493660300794910736859475405192249*x^2 + 368219417368925678040417516301925917412126306519292*x + 691475525517129862790186451321330630700919158856758 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 529063144424448293493660300794910736859475405192249*x

In [173]:
z3 = time.time()
if(validation(A,F,primes_list) & validation(B,F,primes_list)):
    # print 'PublicKey validation: successfull!'
    [EAB,AB] = classGroupEvaluation(A,keyAB1,primes_list,F,p, 'Velu')
    [EBA,BA] = classGroupEvaluation(B,keyBA1,primes_list,F,p, 'Velu')
    print('The isogeny walk of Part1 ends in the curve: ', EBA)
    print('The isogeny walk of Part2 ends in the curve: ', EAB)

    S=sharedSecret(AB,BA)
    print('Shared secret is: ', S)
# else:
    # print 'PublicKey validation: failed!'
z4 = time.time()

[-4, -3, 3, 0, -4, 5, -4, -5, 0, 1, 0, -2, 3, -4, -1, 2, 2, -1, 0, -5, 2, 5, 5, 2, 0, 0, -2, 4, -1, 0, -5]
Isogeny of degree 7 from Elliptic Curve defined by y^2 = x^3 + 596264372037365600245307645802453244071784354902661*x^2 + x over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 596264372037365600245307645802453244071784354902661*x^2 + 157076891920987353140120420455804576759751894083069*x + 899398746386505288810008985932171552429550727920620 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 17 from Elliptic Curve defined by y^2 = x^3 + 596264372037365600245307645802453244071784354902661*x^2 + 157076891920987353140120420455804576759751894083069*x + 899398746386505288810008985932171552429550727920620 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 596264372037365600245307645802453244071784354902661*x^2

Isogeny of degree 73 from Elliptic Curve defined by y^2 = x^3 + 50457497209425949421713490888103121079986874334259*x^2 + 602022900914969531792651972079453000479244744750722*x + 960930466287736773536670397781540411849633017716823 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 50457497209425949421713490888103121079986874334259*x^2 + 1045382033213134668360954218089224285670222131638369*x + 634689647186631638171770704610764821728418010457041 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 107 from Elliptic Curve defined by y^2 = x^3 + 50457497209425949421713490888103121079986874334259*x^2 + 1045382033213134668360954218089224285670222131638369*x + 634689647186631638171770704610764821728418010457041 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 50457497209425949421713490888103121079986874334259*x^2 

Isogeny of degree 41 from Elliptic Curve defined by y^2 = x^3 + 261163109675936965471941961384663659644160294840148*x^2 + 795587428324719318938450413855609699694782323027364*x + 861125110196292950617077284233701747402902028689754 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 261163109675936965471941961384663659644160294840148*x^2 + 827829160960385883002313097185789215021376795787470*x + 920310000162344276890890455317833484048900639962037 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 47 from Elliptic Curve defined by y^2 = x^3 + 261163109675936965471941961384663659644160294840148*x^2 + 827829160960385883002313097185789215021376795787470*x + 920310000162344276890890455317833484048900639962037 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 261163109675936965471941961384663659644160294840148*x^2

Isogeny of degree 17 from Elliptic Curve defined by y^2 = x^3 + 962873958443848052232026723479661650111033506639304*x^2 + x over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 962873958443848052232026723479661650111033506639304*x^2 + 45996831894892084200527781456101557839798056250581*x + 80349563950170642411996302183417288722636688451035 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 83 from Elliptic Curve defined by y^2 = x^3 + 962873958443848052232026723479661650111033506639304*x^2 + 45996831894892084200527781456101557839798056250581*x + 80349563950170642411996302183417288722636688451035 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 962873958443848052232026723479661650111033506639304*x^2 + 1238434685688004835349766836936214332811112854804942*x + 12448561061537511331007281038277693224472857932208

[5, 4, -1, 2, 1, 5, -4, -3, -1, 1, -1, 3, -2, -3, 0, 3, 4, -4, 5, 4, 4, 3, -4, -3, 4, -5, 0, 1, -4, 0, 0]
Isogeny of degree 3 from Elliptic Curve defined by y^2 = x^3 + 506980402902891893139279769335922248598272448676121*x^2 + x over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 506980402902891893139279769335922248598272448676121*x^2 + 1208831408978684833636610934333961828353203939048045*x + 7667047614425713906929263067631263598647814593620 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 5 from Elliptic Curve defined by y^2 = x^3 + 506980402902891893139279769335922248598272448676121*x^2 + 1208831408978684833636610934333961828353203939048045*x + 7667047614425713906929263067631263598647814593620 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 506980402902891893139279769335922248598272448676121*x^2 + 3

Isogeny of degree 37 from Elliptic Curve defined by y^2 = x^3 + 1227100440223508268024707837695384414408847138155756*x^2 + 15716494884365692756829948006620604095761807639100*x + 940396175048912494573343073835589987821928750502418 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 1227100440223508268024707837695384414408847138155756*x^2 + 794209428232591815199082727248258994810655804730511*x + 192293032034149548016626625980348964438265647964860 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 43 from Elliptic Curve defined by y^2 = x^3 + 1227100440223508268024707837695384414408847138155756*x^2 + 794209428232591815199082727248258994810655804730511*x + 192293032034149548016626625980348964438265647964860 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 1227100440223508268024707837695384414408847138155756*

Isogeny of degree 101 from Elliptic Curve defined by y^2 = x^3 + 1027282044171281851480640462768973345616825217213472*x^2 + 853461761300340263832414297779040419795639596385739*x + 66565986744247729052545756770346965326292694900369 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 1027282044171281851480640462768973345616825217213472*x^2 + 849054767143053845893528145435907416057992674393437*x + 1001633455453221053183591484751680179142474262728372 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 19 from Elliptic Curve defined by y^2 = x^3 + 1117251591180142103359294487364385367398639485533986*x^2 + x over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 1117251591180142103359294487364385367398639485533986*x^2 + 1243012582161801701787080849176632960129320886534428*x + 67799515170962703316985505114327634247849

Isogeny of degree 101 from Elliptic Curve defined by y^2 = x^3 + 904820037271621871175056801605446671232037537401998*x^2 + 694174723294119791043188198342216059554706476721380*x + 470702484479772108277225659887242928763198494432224 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 904820037271621871175056801605446671232037537401998*x^2 + 958325961903159945939473268772910586799297467589115*x + 1139258857718687209369763682226826401265117122581078 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 19 from Elliptic Curve defined by y^2 = x^3 + 142488874486374314303246395200994634196246032679712*x^2 + x over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 142488874486374314303246395200994634196246032679712*x^2 + 804897395580084122309186867026246919801927569251898*x + 128713369181664253170339948169806960326182113

Isogeny of degree 73 from Elliptic Curve defined by y^2 = x^3 + 856037024735267686257373122855983731009921094827413*x^2 + 490219916871788650577231941962632633026732284929167*x + 268846421222239691341043237083278170248946934876417 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 856037024735267686257373122855983731009921094827413*x^2 + 837668180256912911343062395885036790495629801754304*x + 801627287782767127218161977858519668871511970087631 over Finite Field of size 1308719482222569797644787830882490714546558590759979
Isogeny of degree 79 from Elliptic Curve defined by y^2 = x^3 + 856037024735267686257373122855983731009921094827413*x^2 + 837668180256912911343062395885036790495629801754304*x + 801627287782767127218161977858519668871511970087631 over Finite Field of size 1308719482222569797644787830882490714546558590759979 to Elliptic Curve defined by y^2 = x^3 + 856037024735267686257373122855983731009921094827413*x^2

In [174]:
timeCSIDH = z4 + z2 - z1- z3
timeCSIDH/(timeT + timeT2)

7.199839099096302

# Comparsion VELU - MONTGOMERY

In [233]:
time2= []
time1 = []
list1 = []
# exponent = [1,1,1]
# exponent2 = [1,1,1]

In [234]:
for cycle_num in range(2,37):
    [primes_list, p,a] = makePrimesList(2*cycle_num) # a == the smallest prime number bigger than the n-th prime number such that
    F = GF(p) #field
    exponent = [1]*len(primes_list)
    keyA = copy(exponent)
    keyBA = copy(keyA)
    keyA1 = copy(keyA)
    keyBA1 = copy(keyA)
    
    exponent2 = [1]*len(primes_list)
    keyB = copy(exponent2)
    keyAB = copy(keyB)
    keyB1 = copy(keyB)
    keyAB1 = copy(keyB)
    
    z1 = time.time()
    EA = MontgomeryCurve(F,T).classGroupEvaluation(keyA,primes_list)
    EB = MontgomeryCurve(F,T).classGroupEvaluation(keyB,primes_list)
    z2 = time.time()
    A = EA.coef()
    B = EB.coef()
    
    z3 = time.time()
    if(EA.is_supersingular(primes_list) & EB.is_supersingular(primes_list)):
        # print 'PublicKey validation: successfull!'
        EAB = MontgomeryCurve(F,A).classGroupEvaluation(keyAB,primes_list)
        EBA = MontgomeryCurve(F,B).classGroupEvaluation(keyBA,primes_list)
       
        AB = EAB.coef()
        BA = EBA.coef()
        S=sharedSecret(AB,BA)
       
    # else:
        # print 'PublicKey validation: failed!'
    z4 = time.time()
    
    timeT = z2 - z1
    timeT2 = z4 - z3
    
    T = 0
    z1 = time.time()
    [EA,A] = classGroupEvaluation(T,keyA1,primes_list,F,p, 'Velu')
    [EB,B] = classGroupEvaluation(T,keyB1,primes_list,F,p, 'Velu')
    z2 = time.time()
    
    z3 = time.time()
    if(validation(A,F,primes_list) & validation(B,F,primes_list)):
        # print 'PublicKey validation: successfull!'
        [EAB,AB] = classGroupEvaluation(A,keyAB1,primes_list,F,p, 'Velu')
        [EBA,BA] = classGroupEvaluation(B,keyBA1,primes_list,F,p, 'Velu')
       
        S=sharedSecret(AB,BA)
    # else:
        # print 'PublicKey validation: failed!'
    z4 = time.time()
    timeCSIDHV = z4 + z2 - z1- z3
    time1.append(timeCSIDHV)
    time2.append(timeT + timeT2)
    rrr = timeCSIDHV/(timeT + timeT2)
    list1.append(rrr)

[1, 1, 1, 1, 1]
Isogeny of degree 5 from Elliptic Curve defined by y^2 = x^3 + x over Finite Field of size 78539 to Elliptic Curve defined by y^2 = x^3 + 48808*x + 66322 over Finite Field of size 78539
Isogeny of degree 7 from Elliptic Curve defined by y^2 = x^3 + 48808*x + 66322 over Finite Field of size 78539 to Elliptic Curve defined by y^2 = x^3 + 34697*x + 5051 over Finite Field of size 78539
Isogeny of degree 11 from Elliptic Curve defined by y^2 = x^3 + 34697*x + 5051 over Finite Field of size 78539 to Elliptic Curve defined by y^2 = x^3 + 70034*x + 7527 over Finite Field of size 78539
Isogeny of degree 17 from Elliptic Curve defined by y^2 = x^3 + 70034*x + 7527 over Finite Field of size 78539 to Elliptic Curve defined by y^2 = x^3 + 53960*x + 59473 over Finite Field of size 78539
[1, 0, 0, 0, 0]
Isogeny of degree 3 from Elliptic Curve defined by y^2 = x^3 + 17258*x^2 + x over Finite Field of size 78539 to Elliptic Curve defined by y^2 = x^3 + 17258*x^2 + 21206*x + 63443 over F

[1, 1, 1, 1, 1, 1, 1, 1, 1]
Isogeny of degree 3 from Elliptic Curve defined by y^2 = x^3 + x over Finite Field of size 19185986819 to Elliptic Curve defined by y^2 = x^3 + 7097450796*x + 7650397328 over Finite Field of size 19185986819
Isogeny of degree 5 from Elliptic Curve defined by y^2 = x^3 + 7097450796*x + 7650397328 over Finite Field of size 19185986819 to Elliptic Curve defined by y^2 = x^3 + 16430086451*x + 17430815804 over Finite Field of size 19185986819
Isogeny of degree 7 from Elliptic Curve defined by y^2 = x^3 + 16430086451*x + 17430815804 over Finite Field of size 19185986819 to Elliptic Curve defined by y^2 = x^3 + 15804303966*x + 10648286490 over Finite Field of size 19185986819
Isogeny of degree 11 from Elliptic Curve defined by y^2 = x^3 + 15804303966*x + 10648286490 over Finite Field of size 19185986819 to Elliptic Curve defined by y^2 = x^3 + 14651071686*x + 9096742573 over Finite Field of size 19185986819
Isogeny of degree 13 from Elliptic Curve defined by y^2 = 

Isogeny of degree 43 from Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 2385757654*x + 9225856730 over Finite Field of size 19185986819 to Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 10792117597*x + 10192555504 over Finite Field of size 19185986819
[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
Isogeny of degree 5 from Elliptic Curve defined by y^2 = x^3 + x over Finite Field of size 14841476269619 to Elliptic Curve defined by y^2 = x^3 + 24635354335*x + 3195443387526 over Finite Field of size 14841476269619
Isogeny of degree 7 from Elliptic Curve defined by y^2 = x^3 + 24635354335*x + 3195443387526 over Finite Field of size 14841476269619 to Elliptic Curve defined by y^2 = x^3 + 10748458216055*x + 9935219479104 over Finite Field of size 14841476269619
Isogeny of degree 11 from Elliptic Curve defined by y^2 = x^3 + 10748458216055*x + 9935219479104 over Finite Field of size 14841476269619 to Elliptic Curve defined by y^2 = x^3 + 3090975494375*x + 14413016464957 over Finite Field of size 1484147626

[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
Isogeny of degree 3 from Elliptic Curve defined by y^2 = x^3 + x over Finite Field of size 37118532150319619 to Elliptic Curve defined by y^2 = x^3 + 14453811744605815*x + 14523181225771380 over Finite Field of size 37118532150319619
Isogeny of degree 7 from Elliptic Curve defined by y^2 = x^3 + 14453811744605815*x + 14523181225771380 over Finite Field of size 37118532150319619 to Elliptic Curve defined by y^2 = x^3 + 20357575347113346*x + 29305347692052766 over Finite Field of size 37118532150319619
Isogeny of degree 11 from Elliptic Curve defined by y^2 = x^3 + 20357575347113346*x + 29305347692052766 over Finite Field of size 37118532150319619 to Elliptic Curve defined by y^2 = x^3 + 13148014667227376*x + 14981036720445054 over Finite Field of size 37118532150319619
Isogeny of degree 13 from Elliptic Curve defined by y^2 = x^3 + 13148014667227376*x + 14981036720445054 over Finite Field of size 37118532150319619 to Elliptic Curve defined by y^2 

[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
Isogeny of degree 5 from Elliptic Curve defined by y^2 = x^3 + x over Finite Field of size 82395230866857848939 to Elliptic Curve defined by y^2 = x^3 + 48126354829814243517*x + 27420695547104227076 over Finite Field of size 82395230866857848939
Isogeny of degree 11 from Elliptic Curve defined by y^2 = x^3 + 48126354829814243517*x + 27420695547104227076 over Finite Field of size 82395230866857848939 to Elliptic Curve defined by y^2 = x^3 + 13705459334513579843*x + 26974638597618527276 over Finite Field of size 82395230866857848939
Isogeny of degree 13 from Elliptic Curve defined by y^2 = x^3 + 13705459334513579843*x + 26974638597618527276 over Finite Field of size 82395230866857848939 to Elliptic Curve defined by y^2 = x^3 + 72380604272616762316*x + 69503463039885545122 over Finite Field of size 82395230866857848939
Isogeny of degree 17 from Elliptic Curve defined by y^2 = x^3 + 72380604272616762316*x + 69503463039885545122 over Finite Fiel

...

Isogeny of degree 167 from Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 4220062626729808620414200423997363555324732691369248550851426791009348244448516139915530914268600658067987455713996380981404232633154003694169553908621*x + 11929170671460211883747090946876541950070237918495384931330165045806768557429230197109087915718781056350265084266292780684902249610720372099856020317333 over Finite Field of size 13696918225230539263776139268185315102196638296197882978729521488718514107243002273037986853834203295671931017193543475107531831957985271415407290225579 to Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 2656181563727246604019612851018968559842357744153384567368801334026508674293695396342588986676817490818563940608638299896838769711499547945156754989602*x + 4872602474110761945323662258867258082627100298709355000642445612106881315693605206079733192158763080835383374996832680997561263183374875365717151646416 over Finite Field of size 13696918225230539263776139268185315102196638296197882978

Isogeny of degree 211 from Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 8636298135490268948743516866106127570846324248862970677131925013622897374547986213745665785554139041295387774529476546898077018023890945675021769173188*x + 2741776579068494159588975612512011222760149065505808050241004830370610077323394386764772604180521269229578848655651942272489177769680233414423731793103 over Finite Field of size 13696918225230539263776139268185315102196638296197882978729521488718514107243002273037986853834203295671931017193543475107531831957985271415407290225579 to Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 9290970618108194993415258058365062509471437443763193383449624959262286679936166426814775103685730407255693799678233322609256422455677297286162447547997*x + 5779831070612746906376899259642640618982803585301542060228651742836266250848054319963405149601527771631226630390626372098382057861741042002049425519491 over Finite Field of size 136969182252305392637761392681853151021966382961978829787

Isogeny of degree 257 from Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 5944372213029096505369832222410779961059109040118716401532684521199270563023513454437541509189658501319299874012050575158306806912427530881947731910754*x + 1194588656585558985383609389915959276863478809131662727844721661121263718961558189535166700311053714073606552311998368329264730882658569313031849019969 over Finite Field of size 13696918225230539263776139268185315102196638296197882978729521488718514107243002273037986853834203295671931017193543475107531831957985271415407290225579 to Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 5658605363358102762547466403203889102210307924355792637254212682735149576921355925580962319615699597022426749383630476703796895414984706229287862074310*x + 11709005645280709278253366334694126898991787898338113904332820077664772366186615734541964557370904003567772210520406758121993434754763427810977157149138 over Finite Field of size 13696918225230539263776139268185315102196638296197882978

Isogeny of degree 307 from Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 6311451908568382050464454459623549078121187925084861091955840394108048647903568671146481918409766169290728893409509685150628638936212296199797290246104*x + 10156716723166741065577457525619807543266857125866230521411836627750231033232342261205101656969899220848960113465622820221123931122333850673186780706646 over Finite Field of size 13696918225230539263776139268185315102196638296197882978729521488718514107243002273037986853834203295671931017193543475107531831957985271415407290225579 to Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 8244746196012159967269600091910885483981787924775241752842827261284787201819424434482608451511385034581533050786661361869864689320427834879713845243281*x + 1586551979060918822622097794585551841519087036592278206420335953670814774884432820111195822912317875436729404141889671752668970592396803980739881962011 over Finite Field of size 13696918225230539263776139268185315102196638296197882978

Isogeny of degree 353 from Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 7932279160692400457153048501437568652380499880532882541650897394760539323014243644446385170388068699026267738664981534883495015294507070526478304621126*x + 2380785231057513726133732245388032224046645262680996712462583103607689853901930823859804079648012605458333114667105496924265507080045452764899552172100 over Finite Field of size 13696918225230539263776139268185315102196638296197882978729521488718514107243002273037986853834203295671931017193543475107531831957985271415407290225579 to Elliptic Curve defined by y^2 = x^3 + 6*x^2 + 685561583338698139058903344738643168793105366038918758653752193974813208269686043508989712957983394343310416526382939824401852886866533654570919035345*x + 5355974898826384356636010365177558730684723552686926446896984028430798027617182051120640488685596134696395060435512989168413546790855293908385027416547 over Finite Field of size 1369691822523053926377613926818531510219663829619788297872

In [236]:
time1

[0.07316422462463379,
 0.08814430236816406,
 0.21088600158691406,
 0.33707571029663086,
 0.40555596351623535,
 0.6309823989868164,
 1.6735801696777344,
 2.156412124633789,
 2.4826409816741943,
 2.4687013626098633,
 3.6160428524017334,
 9.197115659713745,
 5.665929794311523,
 5.825971841812134,
 24.064892053604126,
 11.07352614402771,
 12.68078064918518,
 36.85184383392334,
 38.110931396484375,
 22.101842880249023,
 30.294200897216797,
 54.274927616119385,
 37.134318828582764,
 37.070390462875366,
 45.81946802139282,
 98.94069600105286,
 109.46215319633484,
 179.19797587394714,
 94.50452518463135,
 101.20220637321472,
 228.2701334953308,
 247.00021195411682,
 242.2424659729004,
 265.6630320549011,
 272.80179738998413]

In [237]:
list1

[2.712449728200822,
 3.788261332896139,
 1.5411635565312842,
 2.905253424024166,
 2.571715177280946,
 3.049467257079714,
 5.5520434070757965,
 6.039626029430718,
 5.948683862498093,
 4.344329727352978,
 5.646830681639217,
 11.413571900282621,
 6.261317971854854,
 5.3172225337512105,
 16.884454731773708,
 7.455624127555692,
 7.609073225262953,
 19.590604996567762,
 17.79703813258996,
 8.822595138894572,
 11.292135901898554,
 18.03437729320922,
 10.27896896318396,
 9.947260631755656,
 10.451780034048365,
 22.332881962171896,
 22.185522786623245,
 32.13167414692079,
 15.599518516553688,
 16.37491738238382,
 33.07503673912698,
 32.84060340077837,
 30.413513624348088,
 29.571289940971617,
 28.98322944296175]